In [1]:
import pandas as pd
import numpy as np
from numpy import linspace
import seaborn as sns
import joypy

#plotly
import plotly as py
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

from scipy.stats.kde import gaussian_kde

#bokeh
from bokeh.io import output_file, show
from bokeh.models import ColumnDataSource, FixedTicker, PrintfTickFormatter
from bokeh.plotting import figure
from bokeh.sampledata.perceptions import probly

from sklearn.neighbors import KernelDensity

import matplotlib as mpl
import matplotlib.pyplot as plt
import matplotlib.gridspec as grid_spec
import matplotlib.pylab as plt

import colorcet as cc

In [124]:
pd.options.display.float_format = "{:,.2f}".format

In [96]:
fatal = pd.read_csv('austin_fatalities.csv')
cases = pd.read_csv('austin_cases.csv')

In [97]:
fatal.head(10)

County_Name Population  3/4/20  3/5/20  3/6/20  3/7/20  3/8/20  3/9/20  \
0    Anderson     62,245     0.0     0.0     0.0     0.0     0.0     0.0   
1     Andrews     17,487     0.0     0.0     0.0     0.0     0.0     0.0   
2    Angelina     94,245     0.0     0.0     0.0     0.0     0.0     0.0   
3     Aransas     26,041     0.0     0.0     0.0     0.0     0.0     0.0   
4      Archer      9,847     0.0     0.0     0.0     0.0     0.0     0.0   
5   Armstrong      1,970     0.0     0.0     0.0     0.0     0.0     0.0   
6    Atascosa     55,946     0.0     0.0     0.0     0.0     0.0     0.0   
7      Austin     36,542     0.0     0.0     0.0     0.0     0.0     0.0   
8      Bailey      8,426     0.0     0.0     0.0     0.0     0.0     0.0   
9     Bandera     25,100     0.0     0.0     0.0     0.0     0.0     0.0   

   3/10/20  3/11/20  ...  5/3/20  5/4/20  5/5/20  5/6/20  5/7/20  5/8/20  \
0      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
1      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
2      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
3      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
4      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
5      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
6      0.0      0.0  ...     1.0     1.0     1.0     1.0     1.0     1.0   
7      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
8      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   
9      0.0      0.0  ...     0.0     0.0     0.0     0.0     0.0     0.0   

   5/9/20  5/10/20  5/11/20  5/12/20  
0     0.0      0.0      0.0      0.0  
1     0.0      0.0      0.0      0.0  
2     0.0      0.0      0.0      1.0  
3     0.0      0.0      0.0      0.0  
4     0.0      0.0      0.0      0.0  
5     0.0      0.0      0.0      0.0  
6     1.0      1.0      1.0      1.0  
7     0.0      0.0      0.0      0.0  
8     0.0      0.0      0.0      0.0  
9     0.0      0.0      0.0      0.0  

[10 rows x 72 columns]

In [98]:
cases.head(10)

County_Name Population  3/4/20  3/5/20  3/6/20  3/9/20  3/10/20  3/11/20  \
0    Anderson     62,245     0.0     0.0     0.0     0.0      0.0      0.0   
1     Andrews     17,487     0.0     0.0     0.0     0.0      0.0      0.0   
2    Angelina     94,245     0.0     0.0     0.0     0.0      0.0      0.0   
3     Aransas     26,041     0.0     0.0     0.0     0.0      0.0      0.0   
4      Archer      9,847     0.0     0.0     0.0     0.0      0.0      0.0   
5   Armstrong      1,970     0.0     0.0     0.0     0.0      0.0      0.0   
6    Atascosa     55,946     0.0     0.0     0.0     0.0      0.0      0.0   
7      Austin     36,542     0.0     0.0     0.0     0.0      0.0      0.0   
8      Bailey      8,426     0.0     0.0     0.0     0.0      0.0      0.0   
9     Bandera     25,100     0.0     0.0     0.0     0.0      0.0      0.0   

   3/12/20  3/13/20  ...  5/3/20  5/4/20  5/5/20  5/6/20  5/7/20  5/8/20  \
0      0.0      0.0  ...      32      32      34      38      40      41   
1      0.0      0.0  ...      21      21      21      21      21      21   
2      0.0      0.0  ...      55      55      79      86      93     100   
3      0.0      0.0  ...       2       2       2       2       2       2   
4      0.0      0.0  ...       0       0       0       0       0       0   
5      0.0      0.0  ...       2       2       2       2       2       2   
6      0.0      0.0  ...      19      19      19      21      22      22   
7      0.0      0.0  ...      13      13      13      14      14      14   
8      0.0      0.0  ...       0       0       1       2       2       2   
9      0.0      0.0  ...       6       6       6       6       6       6   

   5/9/20  5/10/20  5/11/20  5/12/20  
0      41       41       41       50  
1      21       21       21       22  
2     100      100      100      117  
3       2        2        2        2  
4       0        0        0        0  
5       2        2        2        2  
6      22       22       24       27  
7      15       15       15       15  
8       2        3        3        3  
9       6        6        6        6  

[10 rows x 69 columns]

In [99]:
#travis county cases dataset
travis = cases.loc[cases['County_Name'] == "Travis"]
cases1 = travis.stack().reset_index()
cases1.columns = ['index','date','population']
cases1 = cases1.iloc[2:]
cases1.head(40)

index     date population
2     226   3/4/20          0
3     226   3/5/20          0
4     226   3/6/20          0
5     226   3/9/20          0
6     226  3/10/20          0
7     226  3/11/20          0
8     226  3/12/20          0
9     226  3/13/20          0
10    226  3/15/20          2
11    226  3/16/20          2
12    226  3/17/20          3
13    226  3/18/20          4
14    226  3/19/20          7
15    226  3/20/20         21
16    226  3/21/20         22
17    226  3/22/20         22
18    226  3/23/20         22
19    226  3/24/20         79
20    226  3/25/20         98
21    226  3/26/20        119
22    226  3/27/20        137
23    226  3/28/20        160
24    226  3/29/20        179
25    226  3/30/20        200
26    226  3/31/20        206
27    226   4/1/20        244
28    226   4/2/20        305
29    226   4/3/20        351
30    226   4/4/20        430
31    226   4/5/20        460
32    226   4/6/20        484
33    226   4/7/20        502
34    226   4/8/20        554
35    226   4/9/20        597
36    226  4/10/20        642
37    226  4/11/20        690
38    226  4/12/20        744
39    226  4/13/20        774
40    226  4/14/20        856
41    226  4/15/20        900

In [100]:
#all cases
all_cases = cases.stack(0).reset_index()
all_cases.columns = ['index','date','population']
#all_cases = cases.iloc[2:]
all_cases = all_cases[all_cases.date != "County_Name"]
all_cases = all_cases[all_cases.date != "Population"]
all_cases.tail()

index     date population
17521    253   5/8/20          1
17522    253   5/9/20          2
17523    253  5/10/20          2
17524    253  5/11/20          2
17525    253  5/12/20          7

In [105]:
#all fatal
all_fatal = fatal.stack(0).reset_index()
all_fatal.columns = ['index','date','population']
#all_cases = cases.iloc[2:]
all_fatal = all_fatal[all_fatal.date != "County_Name"]
all_fatal = all_fatal[all_fatal.date != "Population"]
all_fatal.tail()

index     date population
18283    253   5/8/20          0
18284    253   5/9/20          0
18285    253  5/10/20          0
18286    253  5/11/20          0
18287    253  5/12/20          0

In [104]:
#create a variable/dictionary with the index and the county_name
county_name = dict(cases['County_Name'])
county_name
county_name_fatal = dict(fatal['County_Name'])
county_name_fatal

{0: 'Anderson',
 1: 'Andrews',
 2: 'Angelina',
 3: 'Aransas',
 4: 'Archer',
 5: 'Armstrong',
 6: 'Atascosa',
 7: 'Austin',
 8: 'Bailey',
 9: 'Bandera',
 10: 'Bastrop',
 11: 'Baylor',
 12: 'Bee',
 13: 'Bell',
 14: 'Bexar',
 15: 'Blanco',
 16: 'Borden',
 17: 'Bosque',
 18: 'Bowie',
 19: 'Brazoria',
 20: 'Brazos',
 21: 'Brewster',
 22: 'Briscoe',
 23: 'Brooks',
 24: 'Brown',
 25: 'Burleson',
 26: 'Burnet',
 27: 'Caldwell',
 28: 'Calhoun',
 29: 'Callahan',
 30: 'Cameron',
 31: 'Camp',
 32: 'Carson',
 33: 'Cass',
 34: 'Castro',
 35: 'Chambers',
 36: 'Cherokee',
 37: 'Childress',
 38: 'Clay',
 39: 'Cochran',
 40: 'Coke',
 41: 'Coleman',
 42: 'Collin',
 43: 'Collingsworth',
 44: 'Colorado',
 45: 'Comal',
 46: 'Comanche',
 47: 'Concho',
 48: 'Cooke',
 49: 'Coryell',
 50: 'Cottle',
 51: 'Crane',
 52: 'Crockett',
 53: 'Crosby',
 54: 'Culberson',
 55: 'Dallam',
 56: 'Dallas',
 57: 'Dawson',
 58: 'Deaf Smith',
 59: 'Delta',
 60: 'Denton',
 61: 'DeWitt',
 62: 'Dickens',
 63: 'Dimmit',
 64: 'Donley'

In [107]:
#create a new column called Date and map to the mappings dictionary
all_cases['county_name'] = all_cases['index'].map(county_name)
all_fatal['county_name'] = all_fatal['index'].map(county_name)
all_fatal.tail()

index     date population county_name
18283    253   5/8/20          0      Zavala
18284    253   5/9/20          0      Zavala
18285    253  5/10/20          0      Zavala
18286    253  5/11/20          0      Zavala
18287    253  5/12/20          0      Zavala

In [103]:
#travis county fatalities dataset
travis = fatal.loc[fatal['County_Name'] == "Travis"]
fatal1 = travis.stack().reset_index()
fatal1.columns = ['index','date','population']
fatal1 = fatal1.iloc[2:]
fatal1.head(40)

index     date population
2     226   3/4/20          0
3     226   3/5/20          0
4     226   3/6/20          0
5     226   3/7/20          0
6     226   3/8/20          0
7     226   3/9/20          0
8     226  3/10/20          0
9     226  3/11/20          0
10    226  3/12/20          0
11    226  3/13/20          0
12    226  3/14/20          0
13    226  3/15/20          0
14    226  3/16/20          0
15    226  3/17/20          0
16    226  3/18/20          0
17    226  3/19/20          0
18    226  3/20/20          0
19    226  3/21/20          0
20    226  3/22/20          0
21    226  3/23/20          0
22    226  3/24/20          0
23    226  3/25/20          0
24    226  3/26/20          0
25    226  3/27/20          0
26    226  3/28/20          1
27    226  3/29/20          1
28    226  3/30/20          1
29    226  3/31/20          1
30    226   4/1/20          2
31    226   4/2/20          3
32    226   4/3/20          3
33    226   4/4/20          4
34    226   4/5/20          6
35    226   4/6/20          6
36    226   4/7/20          6
37    226   4/8/20          7
38    226   4/9/20          7
39    226  4/10/20          7
40    226  4/11/20          9
41    226  4/12/20          9

In [108]:
#remove commas and convert pop to float
cases1 = cases1.replace(',','', regex=True)
cases1['population'] = cases1.population.astype(float)
#all_cases
all_cases = all_cases.replace(',','', regex=True)
all_cases['population'] = all_cases.population.astype(float)
#cases1.pct_change(axis=0,fill_method='bfill')

In [109]:
#remove commas and convert pop to float
fatal1 = fatal1.replace(',','', regex=True)
fatal1['population'] = fatal1.population.astype(float)
all_fatal = all_fatal.replace(',','', regex=True)
all_fatal['population'] = all_fatal.population.astype(float)
#cases1.pct_change(axis=0,fill_method='bfill')

In [117]:
#add percent change column
cases1['percent_change'] = cases1.population.pct_change(axis=0,fill_method='bfill')
all_cases['percent_change'] = all_cases.population.pct_change(axis=0,fill_method='bfill')
all_cases.head(50)

index     date  population count_name county_name  percent_change
2       0   3/4/20         0.0   Anderson    Anderson             NaN
3       0   3/5/20         0.0   Anderson    Anderson             NaN
4       0   3/6/20         0.0   Anderson    Anderson             NaN
5       0   3/9/20         0.0   Anderson    Anderson             NaN
6       0  3/10/20         0.0   Anderson    Anderson             NaN
7       0  3/11/20         0.0   Anderson    Anderson             NaN
8       0  3/12/20         0.0   Anderson    Anderson             NaN
9       0  3/13/20         0.0   Anderson    Anderson             NaN
10      0  3/15/20         0.0   Anderson    Anderson             NaN
11      0  3/16/20         0.0   Anderson    Anderson             NaN
12      0  3/17/20         0.0   Anderson    Anderson             NaN
13      0  3/18/20         0.0   Anderson    Anderson             NaN
14      0  3/19/20         0.0   Anderson    Anderson             NaN
15      0  3/20/20         0.0   Anderson    Anderson             NaN
16      0  3/21/20         0.0   Anderson    Anderson             NaN
17      0  3/22/20         0.0   Anderson    Anderson             NaN
18      0  3/23/20         0.0   Anderson    Anderson             NaN
19      0  3/24/20         0.0   Anderson    Anderson             NaN
20      0  3/25/20         0.0   Anderson    Anderson             NaN
21      0  3/26/20         0.0   Anderson    Anderson             NaN
22      0  3/27/20         0.0   Anderson    Anderson             NaN
23      0  3/28/20         0.0   Anderson    Anderson             NaN
24      0  3/29/20         0.0   Anderson    Anderson             NaN
25      0  3/30/20         0.0   Anderson    Anderson             NaN
26      0  3/31/20         0.0   Anderson    Anderson             NaN
27      0   4/1/20         1.0   Anderson    Anderson             inf
28      0   4/2/20         1.0   Anderson    Anderson        0.000000
29      0   4/3/20         1.0   Anderson    Anderson        0.000000
30      0   4/4/20         1.0   Anderson    Anderson        0.000000
31      0   4/5/20         1.0   Anderson    Anderson        0.000000
32      0   4/6/20         1.0   Anderson    Anderson        0.000000
33      0   4/7/20         1.0   Anderson    Anderson        0.000000
34      0   4/8/20         1.0   Anderson    Anderson        0.000000
35      0   4/9/20         2.0   Anderson    Anderson        1.000000
36      0  4/10/20         2.0   Anderson    Anderson        0.000000
37      0  4/11/20         3.0   Anderson    Anderson        0.500000
38      0  4/12/20         3.0   Anderson    Anderson        0.000000
39      0  4/13/20         3.0   Anderson    Anderson        0.000000
40      0  4/14/20         3.0   Anderson    Anderson        0.000000
41      0  4/15/20         4.0   Anderson    Anderson        0.333333
42      0  4/16/20         6.0   Anderson    Anderson        0.500000
43      0  4/17/20         6.0   Anderson    Anderson        0.000000
44      0  4/18/20         6.0   Anderson    Anderson        0.000000
45      0  4/19/20         8.0   Anderson    Anderson        0.333333
46      0  4/20/20         8.0   Anderson    Anderson        0.000000
47      0  4/21/20        10.0   Anderson    Anderson        0.250000
48      0  4/22/20        14.0   Anderson    Anderson        0.400000
49      0  4/23/20        14.0   Anderson    Anderson        0.000000
50      0  4/24/20        16.0   Anderson    Anderson        0.142857
51      0  4/25/20        16.0   Anderson    Anderson        0.000000

In [120]:
#all_cases = all_cases.drop('count_name',axis=1)

index     date  population county_name  percent_change
2          0   3/4/20         0.0    Anderson             NaN
3          0   3/5/20         0.0    Anderson             NaN
4          0   3/6/20         0.0    Anderson             NaN
5          0   3/9/20         0.0    Anderson             NaN
6          0  3/10/20         0.0    Anderson             NaN
...      ...      ...         ...         ...             ...
17521    253   5/8/20         1.0      Zavala             0.0
17522    253   5/9/20         2.0      Zavala             1.0
17523    253  5/10/20         2.0      Zavala             0.0
17524    253  5/11/20         2.0      Zavala             0.0
17525    253  5/12/20         7.0      Zavala             2.5

[17018 rows x 5 columns]

In [111]:
#add percent change column
fatal1['percent_change'] = fatal1.population.pct_change(axis=0,fill_method='bfill')
all_fatal['percent_change'] = all_fatal.population.pct_change(axis=0,fill_method='bfill')
all_fatal.head(50)

index     date  population county_name  percent_change
2       0   3/4/20         0.0    Anderson             NaN
3       0   3/5/20         0.0    Anderson             NaN
4       0   3/6/20         0.0    Anderson             NaN
5       0   3/7/20         0.0    Anderson             NaN
6       0   3/8/20         0.0    Anderson             NaN
7       0   3/9/20         0.0    Anderson             NaN
8       0  3/10/20         0.0    Anderson             NaN
9       0  3/11/20         0.0    Anderson             NaN
10      0  3/12/20         0.0    Anderson             NaN
11      0  3/13/20         0.0    Anderson             NaN
12      0  3/14/20         0.0    Anderson             NaN
13      0  3/15/20         0.0    Anderson             NaN
14      0  3/16/20         0.0    Anderson             NaN
15      0  3/17/20         0.0    Anderson             NaN
16      0  3/18/20         0.0    Anderson             NaN
17      0  3/19/20         0.0    Anderson             NaN
18      0  3/20/20         0.0    Anderson             NaN
19      0  3/21/20         0.0    Anderson             NaN
20      0  3/22/20         0.0    Anderson             NaN
21      0  3/23/20         0.0    Anderson             NaN
22      0  3/24/20         0.0    Anderson             NaN
23      0  3/25/20         0.0    Anderson             NaN
24      0  3/26/20         0.0    Anderson             NaN
25      0  3/27/20         0.0    Anderson             NaN
26      0  3/28/20         0.0    Anderson             NaN
27      0  3/29/20         0.0    Anderson             NaN
28      0  3/30/20         0.0    Anderson             NaN
29      0  3/31/20         0.0    Anderson             NaN
30      0   4/1/20         0.0    Anderson             NaN
31      0   4/2/20         0.0    Anderson             NaN
32      0   4/3/20         0.0    Anderson             NaN
33      0   4/4/20         0.0    Anderson             NaN
34      0   4/5/20         0.0    Anderson             NaN
35      0   4/6/20         0.0    Anderson             NaN
36      0   4/7/20         0.0    Anderson             NaN
37      0   4/8/20         0.0    Anderson             NaN
38      0   4/9/20         0.0    Anderson             NaN
39      0  4/10/20         0.0    Anderson             NaN
40      0  4/11/20         0.0    Anderson             NaN
41      0  4/12/20         0.0    Anderson             NaN
42      0  4/13/20         0.0    Anderson             NaN
43      0  4/14/20         0.0    Anderson             NaN
44      0  4/15/20         0.0    Anderson             NaN
45      0  4/16/20         0.0    Anderson             NaN
46      0  4/17/20         0.0    Anderson             NaN
47      0  4/18/20         0.0    Anderson             NaN
48      0  4/19/20         0.0    Anderson             NaN
49      0  4/20/20         0.0    Anderson             NaN
50      0  4/21/20         0.0    Anderson             NaN
51      0  4/22/20         0.0    Anderson             NaN

In [186]:
#add daily_cases column to each dataframe
all_fatal["daily_cases"] = all_fatal["population"].diff()
fatal1["daily_cases"] = fatal1["population"].diff()
all_cases["daily_cases"] = all_cases["population"].diff()
cases1["daily_cases"] = cases1["population"].diff()

In [123]:
print(f"cases1: ",cases1.dtypes)
print(f"all_cases: ",all_cases.dtypes)
print(f"fatal1: ",fatal1.dtypes)
print(f"all_fatal: ",all_fatal.dtypes)

cases1:  index               int64
date               object
population        float64
percent_change    float64
dtype: object
all_cases:  index               int64
date               object
population        float64
county_name        object
percent_change    float64
dtype: object
fatal1:  index               int64
date               object
population        float64
percent_change    float64
dtype: object
all_fatal:  index               int64
date               object
population        float64
county_name        object
percent_change    float64
dtype: object


In [121]:
#round to 2 decimal places
fatal1['percent_change'] = fatal1.percent_change.round(2)
all_fatal['percent_change'] = all_fatal.percent_change.round(2)
cases1['percent_change'] = cases1.percent_change.round(2)
all_cases['percent_change'] = all_cases.percent_change.round(2)

In [127]:
#line plot
#cases
title = "Daily Percent Increases of Covid Cases - Travis County"
fig = px.line(cases1,
              title=title,
              x="date",
              y="percent_change",
              text="percent_change",
              #color="name", 
              hover_name="percent_change",
              line_shape="spline",
              render_mode="svg"
             )
fig.update_layout(
    legend=dict(
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=12,
            color="black"
        ),
        bgcolor="LightSteelBlue",
        bordercolor="Black",
        borderwidth=1
    )
)
fig.update_traces(textposition='top center') #to change the label positions
fig.show()

#all_cases
title = "Daily Percent Increases of Covid Cases - All Counties"
fig = px.line(all_cases,
              title=title,
              x="date",
              y="percent_change",
              #text="percent_change",
              color="county_name", 
              hover_name="percent_change",
              line_shape="spline",
              render_mode="svg"
             )
fig.update_layout(
    legend=dict(
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=12,
            color="black"
        ),
        bgcolor="LightSteelBlue",
        bordercolor="Black",
        borderwidth=1
    )
)
fig.update_traces(textposition='top center') #to change the label positions
fig.show()

#line plot
title = "Daily Percent Increases of Covid Fatalities - Travis County"
fig = px.line(fatal1,
              title=title,
              x="date",
              y="percent_change", 
              text="percent_change",
              #color="percent_change", 
              hover_name="percent_change",
              line_shape="spline",
              render_mode="svg",
             )
fig.update_layout(
    legend=dict(
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=12,
            color="black"
        ),
        bgcolor="LightSteelBlue",
        bordercolor="Black",
        borderwidth=1
    )
)
fig.update_traces(textposition='top center') #to change the label positions
fig.show()

#all_fatal
title = "Daily Percent Increases of Covid Fatalities - All Counties"
fig = px.line(all_fatal,
              title=title,
              x="date",
              y="percent_change", 
              #text="percent_change",
              color="county_name", 
              hover_name="percent_change",
              line_shape="spline",
              render_mode="svg",
             )
fig.update_layout(
    legend=dict(
        traceorder="normal",
        font=dict(
            family="sans-serif",
            size=12,
            color="black"
        ),
        bgcolor="LightSteelBlue",
        bordercolor="Black",
        borderwidth=1
    )
)
fig.update_traces(textposition='top center') #to change the label positions
fig.show()

In [135]:
#all_fatal
title = "Daily Covid Fatalities - All Counties"
fig = px.bar(all_fatal,
              title=title,
              x="date",
              y="population", 
              text="population",
              color="county_name", 
              hover_name="percent_change"
              #size="population"
             )
fig.show()

#all_fatal
title = "Daily Percent Increases of Covid Fatalities - All Counties"
fig = px.bar(all_fatal,
              title=title,
              x="date",
              y="population", 
              text="percent_change",
              color="county_name", 
              hover_name="percent_change"
              #size="population"
             )
fig.show()

In [200]:
#get averages for percent change from each dataframe
print(f'Daily Averages (3/4 - 5/12): ')

avg_percent_change_cases_travis = cases1.replace([np.inf, -np.inf], np.nan)['percent_change']
avg_daily_cases_travis = cases1.replace([np.inf, -np.inf], np.nan)['daily_cases']
print(f'Travis County (% cases): ', avg_percent_change_cases_travis.mean())
print(f'Travis County (number of cases): ', avg_daily_cases_travis.mean())
print('')

avg_percent_change_cases_all_counties = all_cases.replace([np.inf, -np.inf], np.nan)['percent_change']
avg_daily_cases_all_counties = all_cases.replace([np.inf, -np.inf], np.nan)['daily_cases']
print(f'All Texas Counties (% cases): ', avg_percent_change_cases_all_counties.mean())
print(f'All Texas Counties (number of cases): ', avg_daily_cases_all_counties.mean())
print('')

avg_percent_change_fatalities_travis = fatal1.replace([np.inf, -np.inf], np.nan)['percent_change']
avg_daily_fatalities_travis = fatal1.replace([np.inf, -np.inf], np.nan)['daily_cases']
print(f'Travis County (% fatalities): ', avg_percent_change_fatalities_travis.mean())
print(f'Travis County (number of fatalities): ', avg_daily_fatalities_travis.mean())
print('')

avg_percent_change_fatalities_all_counties = all_fatal.replace([np.inf, -np.inf], np.nan)['percent_change']
avg_daily_fatalities_all_counties = all_fatal.replace([np.inf, -np.inf], np.nan)['daily_cases']
print(f'All Texas Counties (% fatalities): ', avg_percent_change_fatalities_all_counties.mean())
print(f'All Texas Counties (number of fatalities): ', avg_daily_fatalities_all_counties.mean())
print('')

print(f'Cases by Month')
print(f'March Cases Travis County Daily Average Increase: ', 8)
print(f'April Cases Travis County Daily Average Increase: ', 46)
print(f'May Cases Travis County Daily Average Increase: ', 48)
print('')

print(f'Fatailities by Month')
print(f'March Fatalities Travis County Daily Average Increase: ', .037)
print(f'April Fatalities Travis County Daily Average Increase: ', 1.43)
print(f'May Fatalities Travis County Daily Average Increase: ', 1.75)

Daily Averages (3/4 - 5/12): 
Travis County (% cases):  0.16758620689655157
Travis County (number of cases):  32.89393939393939

All Texas Counties (% cases):  0.07029668411867278
All Texas Counties (number of cases):  0.00041135335252982314

Travis County (% fatalities):  0.10911111111111112
Travis County (number of fatalities):  0.9420289855072463

All Texas Counties (% fatalities):  0.0181727037516171
All Texas Counties (number of fatalities):  0.0

Cases by Month
March Cases Travis County Daily Average Increase:  8
April Cases Travis County Daily Average Increase:  46
May Cases Travis County Daily Average Increase:  48

Fatailities by Month
March Fatalities Travis County Daily Average Increase:  0.037
April Fatalities Travis County Daily Average Increase:  1.43
May Fatalities Travis County Daily Average Increase:  1.75
